## Реализация второй версии агента

Основные отличия от предыдущей версии:
1. RAG: агент по своему запросу получает похожие примеры из трейна с оценкой релевантности и объяснением этой оценки
2. Дополнительный агент: получает запрос в поисковик от основного агента и результаты поиска, выдает конкретный ответ на вопрос основного агента с использованием информации из поиска
3. Hint: если агент не уверен в своей оценке, он может проанализировать ответ бейзлайна
4. В промпте нет четких пунктов, по которым нужно оценить релевантность, чтобы избежать ошибок первой версии
5. Вместо flash версии gemini используется pro

In [ ]:
!pip install -q langchain_core
!pip install -q langchain_community
!pip install -q langchain_openai
!pip install -q langgraph
!pip install -q tavily

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.5/65.5 kB 3.3 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
datasets 3.6.0 requires fsspec[http]<=2025.3.0,>=2023.1.0, but you have fsspec 2025.3.2 which is incompatible.
cesium 0.12.4 requires numpy<3.0,>=2.0, but you have numpy 1.26.4 which is incompatible.
bigframes 1.42.0 requires rich<14,>=12.4.4, but you have rich 14.0.0 which is incompatible.
plotnine 0.14.5 requires matplotlib>=3.8.0, but you have matplotlib 3.7.2 which is incompatible.
pandas-gbq 0.28.0 requires google-api-core<3.0.0dev,>=2.10.2, but you have google-api-core 1.34.1 which is incompatible.
mlxtend 0.23.4 requires scikit-learn>=1.3.1, but you have scikit-learn 1.2.2 which is incompatible.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 58.1 MB/s eta 0:00:00:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB

In [ ]:
from langchain_openai import ChatOpenAI
from langgraph.graph import StateGraph, END, MessagesState
from langchain_core.messages import HumanMessage, SystemMessage, AIMessage, ToolMessage
from langchain_community.tools.tavily_search import TavilySearchResults
from langchain_community.vectorstores import InMemoryVectorStore
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain.tools.retriever import create_retriever_tool
from langchain.tools import tool
from langchain.text_splitter import CharacterTextSplitter
from langchain.docstore.document import Document as LangchainDocument
import json
import re
import pandas as pd
import numpy as np
import time
from typing import List, Dict, Any, TypedDict, Annotated, Union, Optional
import operator

last_llm_call_time = 0
LLM_CALL_INTERVAL = 15

TAVILY_API_KEY = "ваш ключ"
search_tool = TavilySearchResults(
    tavily_api_key=TAVILY_API_KEY,
    max_results=3,
    include_answer=True,
    include_raw_content=False
)

/tmp/ipykernel_35/856570601.py:23: LangChainDeprecationWarning: The class `TavilySearchResults` was deprecated in LangChain 0.3.25 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-tavily package and should be used instead. To use it run `pip install -U :class:`~langchain-tavily` and import as `from :class:`~langchain_tavily import TavilySearch``.
  search_tool = TavilySearchResults(


In [ ]:
class AgentState(): # в промпте агента будем собирать:
    def __init__(self, current_task):
        self.search_history = [] # историю поиска: [{'запрос':'ответ от дополнительного агента'}, ...]
        self.rag_context = None # примеры из базы знаний RAG
        self.hint = None # ответ бейзлайна
        self.current_task = current_task # запрос пользователя и информацию об организации
        self.last_query = None
        self.q_count = 0 # нужно для контроля числа запросов

База знаний RAG собиралась следующим образом:
1. Из тренировочного датасета были выбраны первые 100 примеров, в которых первая версия агента допустила ошибки
2. Каждый пример просмотрен вручную, если релевантность была категорически неверной, то она менялась
3. Дабавилась колонка с объяснением релевантности

In [ ]:
import pandas as pd
for_rag = pd.read_csv("/kaggle/input/for_rag.csv")
for_rag

request  \
0    лиственница доска рязанский проспект   
1                              подстанция   
2   минздрав перечень перинатальный центр   
3            где в питере недорого поесть   
4                            обогреватель   
..                                    ...   
95                      Где поесть нателя   
96                      Скаладромы москвы   
97  где в адлере вкусно и недорого поесть   
98                   сход развал братеево   
99                   москва стриптиз клуб   

                                             response  relevance  \
0   [Address]\n  Москва, Привольная улица, 70\n  [...        0.0   
1   [Address]\n  Краснодар, Центральный внутригоро...        1.0   
2   [Address]\n  Московская область, Мытищи, улица...        1.0   
3   [Address]\n  Санкт-Петербург, Большая Морская ...        1.0   
4   [Address]\n  Республика Башкортостан, Уфа, про...        0.0   
..                                                ...        ...   
95  [Address]\n  Ленинградская область, Всеволожск...        1.0   
96  [Address]\n  Москва, Вятская улица, 27, стр. 1...        1.0   
97  [Address]\n  Краснодарский край, Сочи, улица П...        1.0   
98  [Address]\n  Москва, Задонский проезд, 32Ас1\n...        0.0   
99  [Address]\n  Москва, Ленинский проспект, 86\n ...        0.0   

                                          explanation  
0   Географическое расположение: не совпадает (нуж...  
1   Тип места, которое ищет пользователь: совпадае...  
2   Тип места, которое ищет пользователь: совпадае...  
3   Географическое расположение совпадает, услуги ...  
4                Среди товаров не указан обогреватель  
..                                                ...  
95  Вид услуг соответствует, непонятно, что подраз...  
96                 География и вид услуг соотвествуют  
97  География и вид услуг соотвествуют. Среди блюд...  
98  По данным из интернета, не совападает район (Н...  
99                     Нужен был клуб, а найден салон  

[100 rows x 4 columns]

In [ ]:
print(for_rag.iloc[3,-1])

Географическое расположение совпадает, услуги совпадают, в заведении можно недорого поесть (в меню есть недорогие блюда, несмотря на критику высоких цен, которая относится к дорогим блюдам)


In [ ]:
eval_set = pd.read_csv("/kaggle/input/eval_gemini_exp1_exp2.csv")
eval_set

request  \
0                                               сигары   
1                            кальянная спб мероприятия   
2                                             Эпиляция   
3                                     стиральных машин   
4                                сеть быстрого питания   
..                                                 ...   
495                                 наращивание ресниц   
496                                               игры   
497  домашний интернет в курске что подключить отзы...   
498          гостиница волгодонск сауна номер телефона   
499           футбол для подростков в нижнем новгороде   

                                              response  target  \
0    [Address]\n  Москва, Дубравная улица, 34/29\n ...     1.0   
1    [Address]\n  Санкт-Петербург, Большой проспект...     0.0   
2    [Address]\n  Московская область, Одинцово, ули...     1.0   
3    [Address]\n  Москва, улица Обручева, 34/63\n  ...     1.0   
4    [Address]\n  Санкт-Петербург, 1-я Красноармейс...     1.0   
..                                                 ...     ...   
495  [Address]\n  Саратов, улица имени А.С. Пушкина...     1.0   
496  [Address]\n  Москва, Щёлковское шоссе, 79, кор...     0.0   
497  [Address]\n  Курск, Садовая улица, 5\n  [Name]...     0.0   
498  [Address]\n  Ростовская область, городской окр...     0.0   
499  [Address]\n  Нижний Новгород, Ленинский район,...     0.0   

     gemini_2.5_flash_exp1  gemini_2.0_flash_exp2  baseline  
0                      1.0                    1.0       1.0  
1                      0.0                    0.0       0.0  
2                      1.0                    1.0       1.0  
3                      1.0                    1.0       1.0  
4                      1.0                    1.0       1.0  
..                     ...                    ...       ...  
495                    1.0                    0.0       0.0  
496                    1.0                    1.0       1.0  
497                    0.0                    1.0       0.0  
498                    1.0                    1.0       1.0  
499                    0.0                    0.0       0.0  

[500 rows x 6 columns]

In [ ]:
hints = eval_set['baseline']
hints

0      1.0
1      0.0
2      1.0
3      1.0
4      1.0
      ... 
495    0.0
496    1.0
497    0.0
498    1.0
499    0.0
Name: baseline, Length: 500, dtype: float64

In [ ]:
RAW_KNOWLEDGE_BASE = [LangchainDocument(page_content=f"\n[Request]\n{row['request']}\n[Response]\n{row['response'][:1000]}\n[Relevance]\n{row['relevance']}\n[EXPLANATION]\n{row['explanation']}<SEP>", metadata={"explanation": row["explanation"]}) for _, row in for_rag.iterrows()]

In [ ]:
embedding_model = HuggingFaceEmbeddings(
    model_name="intfloat/multilingual-e5-large",
    model_kwargs={"device": "cpu"},
    encode_kwargs={"normalize_embeddings": True},
)

/tmp/ipykernel_35/1121896542.py:1: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embedding_model = HuggingFaceEmbeddings(
2025-07-10 13:08:47.157690: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752152927.373494      35 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752152927.434876      35 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has 

modules.json:   0%|          | 0.00/387 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/57.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/690 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/418 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/201 [00:00<?, ?B/s]

In [ ]:
m = 0
for doc in RAW_KNOWLEDGE_BASE:
    m = max(m, len(doc.page_content))
print(m)

1278


In [ ]:
text_splitter = CharacterTextSplitter(
    separator="<SEP>",
    chunk_size=1500,
    chunk_overlap=0,
    length_function=len,
)

docs_processed = []
for doc in RAW_KNOWLEDGE_BASE:
    docs_processed += text_splitter.split_documents([doc])

In [ ]:
vectorstore = InMemoryVectorStore.from_documents(
    documents=docs_processed, embedding=embedding_model
)
retriever = vectorstore.as_retriever(search_kwargs={"k": 3})

rag_tool = create_retriever_tool(
    retriever,
    "retrieve_task_examples",
    "Найти примеры оценки релевантности, похожие на текущую задачу",
)

In [ ]:
@tool
def get_hint_tool(query):
    """Получить оценку релевантности от другого алгоритма"""
    global current_index
    return hints[current_index]
tools = [search_tool, rag_tool, get_hint_tool]

def call_with_delay(llm, messages): # решение проблемы превышения лимита запросов к моделям в определенный период времени
    global last_llm_call_time
    current_time = time.time()
    if current_time - last_llm_call_time < LLM_CALL_INTERVAL:
        sleep_time = LLM_CALL_INTERVAL - (current_time - last_llm_call_time)
        #print("Ожидание")
        time.sleep(sleep_time)
    #print(messages)
    response = llm.invoke(messages)
    last_llm_call_time = time.time()
    return response

analyst = ChatOpenAI( # основной агент
    base_url="https://generativelanguage.googleapis.com/v1beta/openai/",
    api_key="апи ключ в Google AI Studio",
    model="gemini-2.5-pro", # модель лучше рассуждает
    temperature=0
).bind_tools(tools)

summarizer = ChatOpenAI( # дополнительный агент
    base_url="https://generativelanguage.googleapis.com/v1beta/openai/",
    api_key="апи ключ в Google AI Studio",
    model="gemini-2.5-flash", # модель быстрее и дешевле отвечает
    temperature=0
)

In [ ]:
def search_res_extract(tool_msg: ToolMessage):
    try:
        results = json.loads(tool_msg.content)
        content = ""
        for j, result in enumerate(results[:3]):
            content += f"- Заголовок: {result.get('title', 'Нет данных')}\n"
            result_content = result.get('content', 'Пусто')
            if len(result_content) > 500:
                result_content = result_content[:500] + "..."
            content += f"- Контент: {result_content}\n\n"
        return content
    except Exception as e:
        return f"Ошибка обработки результата поиска: {str(e)}"

def format_search_history(history):
    return "\n\n".join([f"Запрос: {item['query']}\nОтвет: {item['summary']}" for item in history])

def format_rag_context(rag_results: List[LangchainDocument]):
    context = "Примеры похожих оценок релевантности (обрати внимание на логику оценки в объяснениях):\n"
    context+=rag_results
    return context

def extract_answer_number(output):
    if isinstance(output, str):
        match = re.search(r"answer\((\d+)\)", output)
    else:
        match = re.search(r"answer\((\d+)\)", output['messages'][-1].content)
    if match:
        return int(match.group(1))
    else:
        return np.NaN

In [ ]:
def analyst_node(state):
    global agent_state
    #print('='*30)
    #print('Task: ',agent_state.current_task[:50])
    #print('History: ',agent_state.search_history)
    #print('RAG: ',agent_state.rag_context[:30] if agent_state.rag_context is not None else 'NO')
    #print('Hint: ',agent_state.hint)
    rag_use = 0 if agent_state.rag_context is None else 1
    if rag_use==0: # просим агента сначала вызвать rag_tool
        system_content = f"""
Ты - аналитик сервиса Яндекс.Карты
Твоя задача: получить из базы данных RAG примеры похожих оценок релевантности найденного места запросу пользователя
Текущие запрос и найденное место:
{agent_state.current_task}

### Доступные инструменты:
1. RAG: Посмотри похожие примеры оценок релевантности с объяснением оценок

### Алгоритм:
1. Вызови инструмент rag_tool, чтобы получить похожие примеры оценки релевантности. Это важно, чтобы ознакомиться с логикой оценки релевантности на примерах

### Правила:
1. Следуй СТРОГО по алгоритму
2. Вызвать инструмент нужно только один раз
    """
    if rag_use==1:
        system_content = f"""
Ты - аналитик сервиса Яндекс.Карты
Твоя задача: оценить релевантность запроса пользователя найденному месту на карте по шкале от 0 до 1 (доступно только 2 значения)
Раздел 'Текущие запрос и найденное место':
{agent_state.current_task}

### Доступные инструменты:
1. Поиск (Tavily): Найди дополнительную информацию о месте и запросе пользователя, которой не хватает для точной оценки
2. RAG: Посмотри похожие примеры оценок релевантности с объяснением оценок
3. Подсказка: Получи оценку от другого алгоритма в случае неуверенности (она не 100% верная, только с вероятностью 70%). Выдает 0 или 1

### Алгоритм:
1.1 Ты ранее пользовался инструментом rag_tool, обрати внимание на примеры оценки релевантности:
Раздел 'RAG':
{agent_state.rag_context if agent_state.rag_context is not None else "Ты еще не пользовался RAG"}

1.2. Проанализируй примеры из раздела 'RAG' и выясни тонкие моменты логики оценки релевантности. Из каждого из трех примеров выпиши вкратце основные моменты, повлиявшие на оценку релевантности
2.1. Подумай, нужно ли посмотреть дополнительную информацию в интернете, без которой сложно дать точную оценку (Да/Нет). Если Да: Сформулируй вопросы, ответы на которые нужно найти в интернете и переходи к пункту 2.2. Если Нет: переходи к пункту 4
2.2. Проверь, есть ли ответы на эти вопросы в запросе пользователя или в данных организации в разделе 'Текущие запрос и найденное место'
2.3. Проверь есть ли ответы на эти вопросы в разделе 'История поиска' ниже
Раздел 'История поиска':
{format_search_history(agent_state.search_history) if len(agent_state.search_history)>0 else "Ты еще не пользовался поиском"}

3.1. Если все ответы на сформулированные в пункте 2.1 вопросы есть либо в разделе 'Текущие запрос и найденное место' (смотри пункт 2.2), либо в разделе 'История поиска' (смотри пункт 2.3), то переходи к пункту 4. Иначе переходи к пункту 3.2
3.2. Если лимит запросов исчерпан (ты сделал: {agent_state.q_count} из 2 возможных), то попытайся самостоятельно ответить на эти вопросы, используя информацию из 'Истории поиска' и 'Текущих запроса и найденного места' и переходи к пункту 4. Если еще есть доступные запросы, то переходи к пункту 3.3
3.3. Выбери один вопрос из пункта 2.1 и сделай ровно один запрос с помощью инструмента Tavily. Вопрос должен быть сформулирован конкретно в виде вопросительного предложения
4. Используя логику примеров из RAG (смотри пункт 1.2), информацию из запроса и описания места, информацию из истории поиска, сделай предварительную оценку релевантности с объяснением. Напоминание: оценка релевантности - это число 0 или 1
5. Оцени степень своей уверенности по шкале от 0 до 10 с объяснением выбора такой степени
6. Если степень уверенности меньше 5 и ранее ты не запрашивал подсказку (посмотри в раздел 'Подсказка'), то запроси ее с помощью  инструмента get_hint_tool. Если степень уверенности больше или равна 5 и ранее ты не запрашивал подсказку, то переходи к пункту 8. Если ты запрашивал подсказку ранее, то переходи к пункту 7.1
Раздел 'Подсказка'
{agent_state.hint if agent_state.hint is not None else "Ты еще не запрашивал подсказку"}

7.1. Если твое предположение соответствует подсказке, то смело переходи к пункту 8
7.2. Если твое предположение не соответствует подсказке, то обдумай свой ответ еще и иди к следующему пункту алгоритма с обновленной оценкой. Напоминание: подсказка верна с вероятностью 70%, твоя оценка может быть правильной и при этом отличаться от подсказки
8. В качестве ответа предоставь строгий отчет по каждому пункту данного алгоритма и после напиши answer(1) в случае релевантности места запросу и answer(0) в случае нерелевантности

### Правила:
1. Следуй СТРОГО по алгоритму
2. За раз можно вызывать только 1 инструмент
3. Приоритет у информации, полученной в интернете. На отзывы покупателей обращай минимальное внимание
4. Финальный ответ тоже предоставляй в формате, описанном в алгоритме
    """
    prompts = [SystemMessage(content=system_content), HumanMessage(content='Выполни задачу из системного промпта')]
    response = call_with_delay(analyst, prompts) # аналогично первой версии агента, модель видит только промпт со всей нужной информацией без предыдущих шагов с той же целью, что и для первой версии
    #print(response.content)
    #print('='*30)
    return {"messages": [response]}

def summarizer_node(state):
    global agent_state
    #print('='*30)
    last_search_result = ""
    for msg in state['messages']:
        if isinstance(msg, ToolMessage) and msg.name == "tavily_search_results_json":
            last_search_result = search_res_extract(msg)
    #print('LSR: ',last_search_result)
    prompt = [
        SystemMessage(content="Ты - ИИ умного поисковика. Твоя задача - четко ответить на вопрос, используя только предоставленные данные. Если данных поиска недостаточно для ответа, то так и напиши"),
        HumanMessage(content=f"Запрос: {agent_state.last_query}\n\nРезультаты:\n{last_search_result}")
    ]
    response = call_with_delay(summarizer, prompt)
    agent_state.search_history.append({
        'query': agent_state.last_query,
        'summary': response.content
    })
    agent_state.last_query=None
    agent_state.q_count+=1
    #print(response.content)
    #print('='*30)
    return {"messages": [response]}

def tool_node(state):
    global agent_state
    last_message = state['messages'][-1]
    tool_calls = last_message.tool_calls
    tool_messages = []
    for tool_call in tool_calls:
        tool_name = tool_call['name']
        tool_input = tool_call['args']
        current_tool = next((t for t in tools if t.name == tool_name), None)
        if not current_tool:
            continue
        try:
            result = current_tool.invoke(tool_input)
            if tool_name == "tavily_search_results_json":
                agent_state.last_query = tool_input['query']
                tool_messages.append(ToolMessage(
                    content=json.dumps(result),
                    name=tool_name,
                    tool_call_id=tool_call['id']
                ))
            elif tool_name == "retrieve_task_examples":
                formatted_context = format_rag_context(result)
                agent_state.rag_context = formatted_context
                tool_messages.append(ToolMessage(
                    content="RAG OK",
                    name=tool_name,
                    tool_call_id=tool_call['id']
                ))
            elif tool_name == "get_hint_tool":
                agent_state.hint = result
                tool_messages.append(ToolMessage(
                    content=str(result),
                    name=tool_name,
                    tool_call_id=tool_call['id']
                ))
        except Exception as e:
            tool_messages.append(ToolMessage(
                content=f"Ошибка выполнения инструмента: {str(e)}",
                name=tool_name,
                tool_call_id=tool_call['id']
            ))
    return {"messages": tool_messages}

In [ ]:
def router(state):
    if not state['messages']:
        return "analyst"
    last_message = state['messages'][-1]
    if isinstance(last_message, AIMessage) and last_message.tool_calls:
        return "tools"
    elif isinstance(last_message, ToolMessage) and last_message.name == "tavily_search_results_json":
        return "summarizer"
    elif isinstance(last_message, ToolMessage):
        return "analyst"
    elif isinstance(last_message, AIMessage) and "answer(" in last_message.content:
        return "end"
    return "analyst"

def should_summarize(state):
    global agent_state
    if agent_state.last_query:
        return "summarizer"
    return "analyst"

workflow = StateGraph(MessagesState)
workflow.add_node("analyst", analyst_node)
workflow.add_node("tools", tool_node)
workflow.add_node("summarizer", summarizer_node)
workflow.set_entry_point("analyst")
workflow.add_conditional_edges(
    "analyst",
    router,
    {
        "tools": "tools",
        "summarizer": "summarizer",
        "analyst": "analyst",
        "end": END
    }
)
workflow.add_conditional_edges(
    "tools",
    should_summarize
)
workflow.add_edge("summarizer", "analyst")
graph = workflow.compile()

def run_agent_system(example_index):
    global current_index
    global eval_set
    global agent_state
    current_index = example_index
    agent_state.current_task = f"Запрос пользователя: {eval_set.iloc[current_index,0]}\nНайденное место:\n{eval_set.iloc[current_index,1]}"
    input_messages = [HumanMessage(content="Начало")]
    output = graph.invoke({"messages": input_messages})
    return extract_answer_number(output)

In [ ]:
# можно протестировать пайплайн этим кодом (тестировался агент на трейне)
agent_state = AgentState(0)
result = run_agent_system(example_index=498)
print(result)

In [ ]:
from tqdm.auto import tqdm
ans = []
ok=0
for i in tqdm(range(len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/500 [00:00<?, ?it/s]

Task:  Запрос пользователя: сигары
Найденное место:
[Addr
History:  []
RAG:  NO
Hint:  None
[SystemMessage(content='\nТы - аналитик сервиса Яндекс.Карты\nТвоя задача: получить из базы данных RAG примеры похожих оценок релевантности найденного места запросу пользователя\nТекущие запрос и найденное место: \nЗапрос пользователя: сигары\nНайденное место:\n[Address]\n  Москва, Дубравная улица, 34/29\n  [Name]\n  Tabaccos; Магазин Tabaccos; Табаккос\n  [Normalized_name]\n  Магазин табака и курительных принадлежностей\n  [Description]\n  None\n  [Reviews]\n  Организация занимается продажей табака, курительных принадлежностей, вейпов и сопутствующих товаров, а также сувениров и подарков. Отзывы в основном положительные, хвалят ассортимент и обслуживание, но есть замечания по поводу работы персонала и условий оплаты. | 1. Жалуются на отсутствие сигарет | 2. Хвалят большой ассортимент | 3. Отмечают вежливый персонал и наличие табака для кальяна | 4. Критикуют качество товаров и отношение персона

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '13s'}]}}]

In [ ]:
# количество бесплатных запросов в день ограничено, поэтому продолжаем после ошибки лимита на другом аккаунте
from tqdm.auto import tqdm
for i in tqdm(range(35,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/465 [00:00<?, ?it/s]

Task:  Запрос пользователя: китайский посольство
Найденно
History:  []
RAG:  NO
Hint:  None
[SystemMessage(content="\nТы - аналитик сервиса Яндекс.Карты\nТвоя задача: получить из базы данных RAG примеры похожих оценок релевантности найденного места запросу пользователя\nТекущие запрос и найденное место: \nЗапрос пользователя: китайский посольство\nНайденное место:\n[Address]\n  Москва, улица Дружбы, 6\n  [Name]\n  Посольство Китайской Народной Республики; Embassy of the People's Republic of China; Embassy of China; Посольство Китая; Посольство; Posolstvo Kitaya\n  [Normalized_name]\n  Посольство , консульство\n  [Description]\n  None\n  [Reviews]\n  Общий обзор отзывов: Посольство Китайской Народной Республики предоставляет услуги по оформлению виз и консульские услуги, но пользователи жалуются на сложности с получением информации, долгое ожидание и неорганизованность процесса подачи документов. Тональность отзывов преимущественно отрицательная. Хвалят: быстрое принятие документов при 

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '56s'}]}}]

In [ ]:
from tqdm.auto import tqdm
for i in tqdm(range(71,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/429 [00:00<?, ?it/s]

Task:  Запрос пользователя: где в ярославле вкусно и недо
History:  []
RAG:  NO
Hint:  None
[SystemMessage(content="\nТы - аналитик сервиса Яндекс.Карты\nТвоя задача: получить из базы данных RAG примеры похожих оценок релевантности найденного места запросу пользователя\nТекущие запрос и найденное место: \nЗапрос пользователя: где в ярославле вкусно и недорого поесть\nНайденное место:\n[Address]\n  Москва, улица Маросейка, 9\n  [Name]\n  Вкусно — и точка; Vkusno — i tochka; McDonalds; МакДак; Макдоналдс; McDonald's; Vkusno — i Tochka; Мак; Макавто; Макдак; Макдональдс\n  [Normalized_name]\n  Быстрое питание\n  [Description]\n  Ресторан быстрого питания «Вкусно — и точка» предлагает широкий ассортимент блюд, включая бургеры, сеты, картофель фри, наггетсы, напитки и десерты | Биг Спешиал | Биг Хит | Двойной Чизбургер | Чикен Премьер | Сет для двоих | Сет для большой компании | Картофель Фри большой | Наггетсы (9 шт.) | Коктейль Ванильный (бол.) | Латте (сред.) | Тирамису | Айс Де Люкс Виш

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '15s'}]}}]

In [ ]:
from tqdm.auto import tqdm
for i in tqdm(range(109,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/391 [00:00<?, ?it/s]

Task:  Запрос пользователя: mastercard securecode как под
History:  []
RAG:  NO
Hint:  None
[SystemMessage(content='\nТы - аналитик сервиса Яндекс.Карты\nТвоя задача: получить из базы данных RAG примеры похожих оценок релевантности найденного места запросу пользователя\nТекущие запрос и найденное место: \nЗапрос пользователя: mastercard securecode как подключить\nНайденное место:\n[Address]\n  Москва, улица Бахрушина, 32, стр. 1\n  [Name]\n  Банк ВТБ; VTB Bank; VTB; ВТБ; Банк ВТБ, отделение; Vtb; Vtb Bank; Vtb Bank, branch\n  [Normalized_name]\n  Банк\n  [Description]\n  None\n  [Reviews]\n  Банк ВТБ предоставляет различные банковские услуги. Отзывы смешанные: много положительных, но есть и отрицательные. Хвалят: быстрое и качественное обслуживание, профессионализм сотрудников, удобные условия. Критикуют: долгое время ожидания, неэффективную работу электронной очереди, некомпетентность некоторых сотрудников.\n\n| 1. Всё понравилось | 2. Отличное обслуживание | 3. Долгое обслуживание | 

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '23s'}]}}]

In [ ]:
from tqdm.auto import tqdm
for i in tqdm(range(143,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/357 [00:00<?, ?it/s]

Task:  Запрос пользователя: пункты отправки через юлу в г
History:  []
RAG:  NO
Hint:  None
[SystemMessage(content='\nТы - аналитик сервиса Яндекс.Карты\nТвоя задача: получить из базы данных RAG примеры похожих оценок релевантности найденного места запросу пользователя\nТекущие запрос и найденное место: \nЗапрос пользователя: пункты отправки через юлу в городе кинешма\nНайденное место:\n[Address]\n  Ивановская область, Кинешма, Пионерская улица, 2/66\n  [Name]\n  Отделение почтовой связи Кинешма 155810; Otdeleniye pochtovoy svyazi Kineshma 155810; Почта № 155810; Отделение почтовой связи № 155810; Почта России; Почта россии\n  [Normalized_name]\n  Почтовое отделение\n  [Description]\n  None\n  [Reviews]\n  Организация занимается почтовыми услугами, включая выдачу посылок и писем. Отзывы смешанные: много положительных отзывов о персонале и обслуживании, но также есть жалобы на график работы, очереди и некомпетентность сотрудников. | 1. Положительный отзыв без подробностей. | 2. Критикую

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '31s'}]}}]

In [ ]:
# продолжим с упрощенным выводом
from tqdm.auto import tqdm
ok=149
for i in tqdm(range(180,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/320 [00:00<?, ?it/s]

0.8232044198895028 0 1.0
0.8186813186813187 1 0.0
0.819672131147541 1 1.0
0.8152173913043478 1 0.0
0.8162162162162162 0 0.0
0.8172043010752689 1 1.0
0.8181818181818182 1 1.0
0.8191489361702128 1 1.0
0.8201058201058201 1 1.0
0.8157894736842105 1 0.0
0.8167539267015707 1 1.0
0.8177083333333334 1 1.0
0.8186528497409327 0 0.0
0.8195876288659794 0 0.0
0.8153846153846154 1 0.0
0.8163265306122449 1 1.0
0.8121827411167513 1 0.0
0.8131313131313131 0 0.0
0.8140703517587939 1 1.0
0.815 1 1.0
0.8159203980099502 0 0.0
0.8168316831683168 1 1.0
0.812807881773399 1 0.0
0.8137254901960784 1 1.0
0.8146341463414634 1 1.0
0.8106796116504854 0 1.0
0.8115942028985508 1 1.0
0.8125 1 1.0
0.8133971291866029 0 0.0
0.8142857142857143 1 1.0
0.8104265402843602 0 1.0
0.8113207547169812 1 1.0
0.812206572769953 1 1.0
0.8130841121495327 1 1.0
0.813953488372093 0 0.0


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '46s'}]}}]

In [ ]:
# качество резко начало падать, поэтому расширим вывод в консоль
from tqdm.auto import tqdm
ok=175
for i in tqdm(range(215,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/285 [00:00<?, ?it/s]


**1.2. Анализ примеров из RAG:**

*   **Пример 1 (турбаза коктебель -> Родина):** Основной фактор — несоответствие географии. Запрос был на "Коктебель", а найдено место в "посёлке Курортное". Это делает место нерелевантным.
*   **Пример 2 (отели черноморское побережье кудепста -> GreenWood):** География совпадает (Джанхот находится на Черноморском побережье), и тип организации (гостиница) соответствует запросу "отели". Это делает место релевантным.
*   **Пример 3 (Солярии -> Каскад):** Хотя основная категория "Парикмахерская", в описании упоминаются косметологические услуги и эпиляция. Это позволяет сделать вывод, что в салоне красоты такого типа с большой вероятностью может быть и солярий, что делает его релевантным.

**2.1. Необходимость дополнительной информации:**

Да, нужна дополнительная информация.

*   **Вопрос:** Предлагает ли база отдыха "CanadaHouse" услуги, связанные с рыбалкой, или находится ли она в непосредственной близости от водоема, где возможна рыбалка?

**2.2. Пров

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '55s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=201
for i in tqdm(range(252,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/248 [00:00<?, ?it/s]


**1.2. Анализ примеров из RAG**

*   **Пример 1 (Медкомиссия):** Оценка 0.0. Причина: Несоответствие услуги. Пользователь искал конкретную услугу (медкомиссия для прав), а найдена клиника широкого профиля, где данной услуги может не быть.
*   **Пример 2 (ГАИ):** Оценка 1.0. Причина: Соответствие категории. Пользователь искал обобщенное "центральное ГАИ", а найдено районное отделение ГИБДД, что является релевантным уточнением.
*   **Пример 3 (Доска):** Оценка 0.0. Причина: Географическое несоответствие. Пользователь указал конкретный проспект, а организация найдена на другой улице.

**2.1. Необходимость дополнительной информации**

Да, необходима дополнительная информация. Основные расхождения между запросом и найденным местом — это название ("разрешительный отдел" против "центра алкогольного лицензирования") и адрес ("Литовский бульвар" против "Профсоюзная улица"). Нужно выяснить, какой именно разрешительный отдел находится на Литовском бульваре, чтобы понять природу запроса пользоват

RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'model': 'gemini-2.5-pro', 'location': 'global'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '27s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=229
for i in tqdm(range(290,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/210 [00:00<?, ?it/s]

0.7903780068728522 1 1.0
0.791095890410959 0 0.0
0.7918088737201365 0 0.0
0.7925170068027211 1 1.0
0.7932203389830509 1 1.0
0.793918918918919 0 0.0
0.7946127946127947 0 0.0
0.7953020134228188 0 0.0
0.7959866220735786 0 0.0
0.7966666666666666 0 0.0
0.7973421926910299 1 1.0
0.7980132450331126 0 0.0
0.7953795379537953 0 1.0
0.7960526315789473 1 1.0
0.7934426229508197 0 1.0
0.7908496732026143 0 1.0
0.7882736156351792 1 0.0
0.788961038961039 1 1.0
0.7864077669902912 0 1.0
0.7870967741935484 1 1.0
0.7877813504823151 1 1.0
0.7884615384615384 0 0.0
0.7891373801916933 1 1.0
0.7898089171974523 0 0.0
0.7904761904761904 1 1.0
0.7879746835443038 0 1.0
0.7854889589905363 0 1.0
0.7861635220125787 1 1.0
0.786833855799373 1 1.0
0.7875 1 1.0
0.7881619937694704 0 0.0
0.7888198757763976 1 1.0
0.7894736842105263 1 1.0
0.7901234567901234 1 1.0
0.7876923076923077 0 1.0
0.7852760736196319 0 1.0
0.7859327217125383 0 0.0
0.7865853658536586 0 0.0


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '36s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=258
for i in tqdm(range(328,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/172 [00:00<?, ?it/s]

0.7872340425531915 1 1.0
0.7878787878787878 0 0.0
0.7885196374622356 1 1.0
0.7891566265060241 1 1.0
0.7897897897897898 1 1.0
0.7904191616766467 0 0.0
0.7910447761194029 1 1.0
0.7916666666666666 1 1.0
0.7922848664688428 1 1.0
0.7928994082840237 1 1.0
0.7935103244837758 0 0.0
0.7941176470588235 1 1.0
0.7947214076246334 1 1.0
0.7923976608187134 1 0.0
0.793002915451895 1 1.0
0.7936046511627907 0 0.0
0.7942028985507247 1 1.0
0.7947976878612717 0 0.0
0.7953890489913544 1 1.0
0.7959770114942529 1 1.0
0.7936962750716332 1 0.0
0.7942857142857143 1 1.0
0.7948717948717948 0 0.0
0.7954545454545454 1 1.0
0.7932011331444759 1 0.0
0.7937853107344632 1 1.0
0.7943661971830986 0 0.0
0.7949438202247191 1 1.0
0.7955182072829131 1 1.0
0.7960893854748603 1 1.0
0.7966573816155988 1 1.0
0.7972222222222223 0 0.0
0.7977839335180056 0 0.0
0.7955801104972375 1 0.0
0.7961432506887053 1 1.0
0.7939560439560439 1 0.0
0.7945205479452054 1 1.0


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'model': 'gemini-2.5-pro', 'location': 'global'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '29s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=290
for i in tqdm(range(365,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/135 [00:00<?, ?it/s]

0.7923497267759563 0 1.0
0.7929155313351499 1 1.0
0.7934782608695652 1 1.0
0.7940379403794038 0 0.0
0.7945945945945946 1 1.0
0.7951482479784366 1 1.0
0.793010752688172 0 1.0
0.7935656836461126 0 0.0
0.7941176470588235 1 1.0
0.7946666666666666 1 1.0
0.7952127659574468 1 1.0
0.7931034482758621 0 1.0
0.7936507936507936 1 1.0
0.7941952506596306 1 1.0
0.7947368421052632 1 1.0
0.7952755905511811 1 1.0
0.7931937172774869 0 1.0
0.7911227154046997 1 0.0
0.7890625 0 1.0
0.7896103896103897 1 1.0
0.7901554404145078 1 1.0
0.7881136950904393 0 1.0
0.7860824742268041 1 0.0
0.7866323907455013 1 1.0
0.7871794871794872 1 1.0
0.7877237851662404 1 1.0
0.7857142857142857 0 1.0
0.7862595419847328 0 0.0
0.7868020304568528 0 0.0
0.7873417721518987 1 1.0
0.7878787878787878 0 0.0
0.7884130982367759 1 1.0
0.7889447236180904 1 1.0
0.7894736842105263 1 1.0
0.79 0 0.0
0.7905236907730673 1 1.0
0.7910447761194029 1 1.0


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'model': 'gemini-2.5-pro', 'location': 'global'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '2s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=318
for i in tqdm(range(402,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/98 [00:00<?, ?it/s]

0.7915632754342432 1 1.0
0.7896039603960396 0 1.0
0.7901234567901234 1 1.0
0.7881773399014779 0 1.0
0.7886977886977887 0 0.0
0.7892156862745098 1 1.0
0.7897310513447433 1 1.0
0.7902439024390244 1 1.0
0.7907542579075426 1 1.0
0.7888349514563107 1 0.0
0.7869249394673123 0 1.0
0.7874396135265701 0 0.0
0.7879518072289157 1 1.0
0.7884615384615384 0 0.0
0.7889688249400479 1 1.0
0.7894736842105263 1 1.0
0.7899761336515513 1 1.0
0.7904761904761904 1 1.0
0.7909738717339667 1 1.0
0.7914691943127962 1 1.0
0.7919621749408984 1 1.0
0.7924528301886793 0 0.0
0.7929411764705883 1 1.0
0.7934272300469484 1 1.0
0.7939110070257611 0 0.0
0.794392523364486 1 1.0
0.7925407925407926 0 1.0
0.7930232558139535 0 0.0
0.7935034802784223 1 1.0
0.7939814814814815 0 0.0
0.7944572748267898 0 0.0
0.7949308755760369 1 1.0
0.7954022988505747 0 0.0
0.7958715596330275 0 0.0


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '0s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=347
for i in tqdm(range(436,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/64 [00:00<?, ?it/s]

0.7963386727688787 1 1.0
0.7968036529680366 1 1.0
0.7972665148063781 1 1.0
0.7954545454545454 0 1.0
0.7936507936507936 0 1.0
0.7941176470588235 0 0.0
0.7945823927765236 1 1.0
0.795045045045045 1 1.0
0.7955056179775281 1 1.0
0.7937219730941704 1 0.0
0.7941834451901566 1 1.0
0.7924107142857143 1 0.0
0.7928730512249443 0 0.0
0.7933333333333333 1 1.0
0.7937915742793792 0 0.0
0.7942477876106194 1 1.0
0.7947019867549668 1 1.0
0.7929515418502202 0 1.0
0.7912087912087912 1 0.0
0.7916666666666666 0 0.0
0.7921225382932167 1 1.0
0.7925764192139738 1 1.0
0.7930283224400871 1 1.0
0.7934782608695652 1 1.0
0.7917570498915402 0 1.0
0.79004329004329 0 1.0
0.7883369330453563 1 0.0
0.7887931034482759 0 0.0
0.7870967741935484 1 0.0
0.7854077253218884 0 1.0
0.7858672376873662 0 0.0
0.7863247863247863 1 1.0
0.7867803837953091 0 0.0
0.7872340425531915 0 0.0
0.7876857749469215 0 0.0
0.788135593220339 1 1.0


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'model': 'gemini-2.5-pro', 'location': 'global'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '40s'}]}}]

In [ ]:
from tqdm.auto import tqdm
ok=372
for i in tqdm(range(472,len(eval_set))):
    agent_state = AgentState(0)
    result = run_agent_system(example_index=i)
    if result==eval_set.iloc[i,2]:
        ok+=1
    ans.append(result)
    print(ok/len(ans), result, eval_set.iloc[i,2])

  0%|          | 0/28 [00:00<?, ?it/s]

0.7885835095137421 0 0.0
0.7890295358649789 0 0.0
0.7894736842105263 1 1.0
0.7899159663865546 0 0.0
0.790356394129979 0 0.0
0.7887029288702929 1 0.0
0.7870563674321504 0 1.0
0.7875 1 1.0
0.7858627858627859 0 1.0
0.7863070539419087 0 0.0
0.7867494824016563 1 1.0
0.7871900826446281 0 0.0
0.7876288659793814 0 0.0
0.7880658436213992 0 0.0
0.7885010266940452 0 0.0
0.7889344262295082 0 0.0
0.787321063394683 1 0.0
0.7857142857142857 0 1.0
0.7841140529531568 1 0.0
0.782520325203252 1 0.0
0.7829614604462475 0 0.0
0.7834008097165992 1 1.0
0.7838383838383839 1 1.0
0.7842741935483871 1 1.0
0.7826961770623743 1 0.0
0.7811244979919679 1 0.0
0.779559118236473 1 0.0
0.78 0 0.0


## Accuracy второй версии агента: 0.78 (лучше всех предыдущих экспериментов)

## Но было замечено, что ответ агента, несмотря на установленную нулевую температуру, недетерминирован и иногда он может выдать разные ответы
## Поэтому проведем эксперимент: узнаем, насколько может подняться accuracy, если дать возможность агенту еще раз ответить в случаях, в которых он ошибся ранее (он не будет знать, что ошибался на них; ничего в агенте не меняем)

In [ ]:
last_ind = 0
new_ok = 390
for i in tqdm(range(len(ans))):
    if ans[i]!=eval_set.iloc[i,2]:
        agent_state = AgentState(0)
        result = run_agent_system(example_index=i)
        if result==eval_set.iloc[i,2]:
            new_ok+=1
            ans[i]=result
            print(new_ok/len(ans))
    last_ind+=1

  0%|          | 0/500 [00:00<?, ?it/s]

0.782
0.784


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '28s'}]}}]

In [ ]:
# аналогично фиксируем last_ind и new_ok, чтобы продолжить на другом аккаунте
from tqdm.auto import tqdm
last_ind = 27
new_ok = 392
for i in tqdm(range(28, len(ans))):
    if ans[i]!=eval_set.iloc[i,2]:
        agent_state = AgentState(0)
        result = run_agent_system(example_index=i)
        if result==eval_set.iloc[i,2]:
            new_ok+=1
            ans[i]=result
            print(new_ok/len(ans))
    last_ind+=1

  0%|          | 0/472 [00:00<?, ?it/s]

0.786
0.788
0.79
0.792
0.794
0.796
0.798
0.8


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '45s'}]}}]

In [ ]:
from tqdm.auto import tqdm
last_ind = 193
new_ok = 400
for i in tqdm(range(194, len(ans))):
    if ans[i]!=eval_set.iloc[i,2]:
        agent_state = AgentState(0)
        result = run_agent_system(example_index=i)
        if result==eval_set.iloc[i,2]:
            new_ok+=1
            ans[i]=result
            print(new_ok/len(ans))
    last_ind+=1

  0%|          | 0/306 [00:00<?, ?it/s]

0.802
0.804
0.806
0.808
0.81
0.812
0.814
0.816
0.818
0.82


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '11s'}]}}]

In [ ]:
from tqdm.auto import tqdm
last_ind = 323
new_ok = 410
for i in tqdm(range(324, len(ans))):
    if ans[i]!=eval_set.iloc[i,2]:
        agent_state = AgentState(0)
        result = run_agent_system(example_index=i)
        if result==eval_set.iloc[i,2]:
            new_ok+=1
            ans[i]=result
            print(new_ok/len(ans))
    last_ind+=1

  0%|          | 0/176 [00:00<?, ?it/s]

0.822
0.824
0.826
0.828
0.83
0.832
0.834


RateLimitError: Error code: 429 - [{'error': {'code': 429, 'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits.', 'status': 'RESOURCE_EXHAUSTED', 'details': [{'@type': 'type.googleapis.com/google.rpc.QuotaFailure', 'violations': [{'quotaMetric': 'generativelanguage.googleapis.com/generate_content_free_tier_requests', 'quotaId': 'GenerateRequestsPerDayPerProjectPerModel-FreeTier', 'quotaDimensions': {'location': 'global', 'model': 'gemini-2.5-pro'}, 'quotaValue': '100'}]}, {'@type': 'type.googleapis.com/google.rpc.Help', 'links': [{'description': 'Learn more about Gemini API quotas', 'url': 'https://ai.google.dev/gemini-api/docs/rate-limits'}]}, {'@type': 'type.googleapis.com/google.rpc.RetryInfo', 'retryDelay': '44s'}]}}]

In [ ]:
from tqdm.auto import tqdm
last_ind = 460
new_ok = 417
for i in tqdm(range(461, len(ans))):
    if ans[i]!=eval_set.iloc[i,2]:
        agent_state = AgentState(0)
        result = run_agent_system(example_index=i)
        if result==eval_set.iloc[i,2]:
            new_ok+=1
            ans[i]=result
            print(new_ok/len(ans))
    last_ind+=1

  0%|          | 0/39 [00:00<?, ?it/s]

0.836
0.838
0.84


In [ ]:
print(last_ind, new_ok)

499 420


In [ ]:
print(ans)

[1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 1, 1, 1, 

In [ ]:
ok_b = 0
ok_0 = 0
ok_1 = 0
for i in range(len(ans)):
    if eval_set.iloc[i,3]==eval_set.iloc[i,2]:
        ok_0+=1
    if eval_set.iloc[i,4]==eval_set.iloc[i,2]:
        ok_1+=1
    if eval_set.iloc[i,5]==eval_set.iloc[i,2]:
        ok_b+=1
print(ok_b/(len(ans)),ok_0/(len(ans)),ok_1/(len(ans)))

0.71 0.764 0.684


In [ ]:
ok_2 = 0
for i in range(len(ans)):
    if ans[i]==eval_set.iloc[i,2]:
        ok_2+=1
print(ok_2/len(ans), ok_2, len(ans))

0.84 420 500


## Accuracy "хитрой" переоценки: 0.84

In [ ]:
for i in range(len(ans)):
    ans[i] = float(ans[i])

In [ ]:
eval_set['improved_v2'] = ans

In [ ]:
eval_set

request  \
0                                               сигары   
1                            кальянная спб мероприятия   
2                                             Эпиляция   
3                                     стиральных машин   
4                                сеть быстрого питания   
..                                                 ...   
495                                 наращивание ресниц   
496                                               игры   
497  домашний интернет в курске что подключить отзы...   
498          гостиница волгодонск сауна номер телефона   
499           футбол для подростков в нижнем новгороде   

                                              response  target  \
0    [Address]\n  Москва, Дубравная улица, 34/29\n ...     1.0   
1    [Address]\n  Санкт-Петербург, Большой проспект...     0.0   
2    [Address]\n  Московская область, Одинцово, ули...     1.0   
3    [Address]\n  Москва, улица Обручева, 34/63\n  ...     1.0   
4    [Address]\n  Санкт-Петербург, 1-я Красноармейс...     1.0   
..                                                 ...     ...   
495  [Address]\n  Саратов, улица имени А.С. Пушкина...     1.0   
496  [Address]\n  Москва, Щёлковское шоссе, 79, кор...     0.0   
497  [Address]\n  Курск, Садовая улица, 5\n  [Name]...     0.0   
498  [Address]\n  Ростовская область, городской окр...     0.0   
499  [Address]\n  Нижний Новгород, Ленинский район,...     0.0   

     gemini_2.5_flash_exp1  gemini_2.0_flash_exp2  baseline  improved_v2  
0                      1.0                    1.0       1.0          1.0  
1                      0.0                    0.0       0.0          0.0  
2                      1.0                    1.0       1.0          1.0  
3                      1.0                    1.0       1.0          1.0  
4                      1.0                    1.0       1.0          1.0  
..                     ...                    ...       ...          ...  
495                    1.0                    0.0       0.0          1.0  
496                    1.0                    1.0       1.0          1.0  
497                    0.0                    1.0       0.0          0.0  
498                    1.0                    1.0       1.0          1.0  
499                    0.0                    0.0       0.0          0.0  

[500 rows x 7 columns]

In [ ]:
eval_set.to_csv('eval_gemini_final.csv',index=False)

Данная архитектура агента (или скорее агентной системы) явно лучше справляется с задачей, чем неагентный бейзлайн и предыдущие примитивные агенты. А последний эксперимент показал, что у такого варианта агента есть потенциал: можно стабилизировать его улучшенным промптом, в котором будет больше правил для оценки релевантности и приведены примеры типичных ошибок агента.

Примеры типичных ошибок:

*   Неправильная интерпретация запроса пользователя: купить выпечку свежий хлеб -> магазин продуктов - нерелевантно, так как у этого магазина название не "Свежий хлеб", который по информации из интернета существует (очевидно, неверно)
*   Глупые ошибки в логике: магазин -> аптека - релевантно, так как запрос слишком общий, а аптека своего рода магазин (очевидно, неверно)
*   Уделяет внимание незначительным деталям: онлайн страховка -> офис страховой компании, которая предоставляет услуги онлайн страхования - нерелевантно, так как пользователь искал именно онлайн сервис, а не конкретное место на карте (с точки зрения задачи, неверно)

## Перспективы

В теории, добиться скора выше 0.85 можно такой системой если:
1. Убрать тул get_hint_tool (его агент почти не использовал; скор бейзлайна слишком низок для опоры)
2. Убрать RAG или усовершенствовать его (переразметить трейн, добавить более подробное объяснение, выдавать больше примеров, вызывать вспомогательным агентом - недорогой и быстрой моделью). Но рациональнее и быстрее первый вариант
3. Взять более продвинутую LLM (например, GPT 4 или DeepSeek R1)
4. Оставить вспомогательного агента, он хорошо суммаризировал результаты поиска, чтобы промпт основного агента сильно не засорялся
5. Очевидно, поработать над промптом
6. Добавить несколько тулов поиска, потому что tavily часто не выдавал нужный результат
7. Дополнительно переразметить тестовый датасет, чтобы убрать оставшиеся явные несостыковки

Упор лучше сделать на 3 и 5 пункты, данная задача, вероятно, не требует хитрого пайплайна